![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Inżynieria uczenia maszynowego </h1>
<h2> 8. <i>MLFlow</i>  [laboratoria]</h2> 
<h3> Tomasz Ziętkiewicz (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

 ## MLflow
 </br><img style="width: 50%;" src="img/expcontrol/mlflow-logo-d.png"/>

  - https://mlflow.org/
  - Narzędzie podobne do omawianego na poprzednich zajęciach Sacred
  - Nieco inne podejście: mniej ingerencji w istniejący kod
  - Bardziej kompleksowe rozwiązanie: 4 komponenty, pierwszy z nich ma funkcjonalność podobną do Sacred
  - Działa "z każdym" językiem. A tak naprawdę: Python, R, Java + CLI API + REST API
  - Popularna wśród pracodawców - wyniki wyszukiwania ofert pracy: 20 ofert (https://pl.indeed.com/), 36 ofert (linkedin). Sacred: 0
  - Integracja z licznymi bibliotekami / chmurami
  - Rozwiązanie OpenSource, stworzone przez firmę Databricks
  - Dostępna [odpłatna wersja "Managed"](https://databricks.com/product/managed-mlflow) (w ordóżnieniu od "self-hosted")


## Komponenty

MLflow składa się z czterech niezależnych komponentów:
 - **MLflow Tracking** - pozwala śledzić zmiany parametrów, kodu, środowiska i ich wpływ na metryki. Jest to funkcjonalność bardzo zbliżona do tej, którą zapewnia Sacred
 - **MLflow Projects** - umożliwia "pakowanie" kodu ekserymentów w taki sposób, żeby mogłby być w łatwy sposób zreprodukowane przez innych
 - **MLflow Models** - ułatwia "pakowanie" modeli uczenia maszynowego
 - **MLflow Registry** - zapewnia centralne miejsce do przechowywania i współdzielenia modeli. Zapewnia narzędzia do wersjonowania i śledzenia pochodzenia tych modeli.
 
Komponenty te mogą być używane razem bądź oddzielnie.

## MLflow Tracking - przykład
(poniższe przykłady kodu trenującego pochodzą z tutoriala MLflow: https://mlflow.org/docs/latest/tutorials-and-examples/tutorial.html)

In [1]:
%%capture null
!pip install mlflow
!pip install sklearn

In [80]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/train.py
# The data set used in this example is from http://archive.ics.uci.edu/ml/datasets/Wine+Quality
# P. Cortez, A. Cerdeira, F. Almeida, T. Matos and J. Reis.
# Modeling wine preferences by data mining from physicochemical properties. In Decision Support Systems, Elsevier, 47(4):547-553, 2009.

import os
import warnings
import sys

import pandas as pd
import numpy as np
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from sklearn.model_selection import train_test_split
from sklearn.linear_model import ElasticNet
from urllib.parse import urlparse
import mlflow
import mlflow.sklearn

import logging

logging.basicConfig(level=logging.WARN)
logger = logging.getLogger(__name__)

mlflow.set_tracking_uri("http://localhost:5000")
mlflow.set_experiment("s123456")

def eval_metrics(actual, pred):
    rmse = np.sqrt(mean_squared_error(actual, pred))
    mae = mean_absolute_error(actual, pred)
    r2 = r2_score(actual, pred)
    return rmse, mae, r2


if __name__ == "__main__":
    warnings.filterwarnings("ignore")
    np.random.seed(40)

    # Read the wine-quality csv file from the URL
    csv_url = (
        "http://archive.ics.uci.edu/ml/machine-learning-databases/wine-quality/winequality-red.csv"
    )
    try:
        data = pd.read_csv(csv_url, sep=";")
    except Exception as e:
        logger.exception(
            "Unable to download training & test CSV, check your internet connection. Error: %s", e
        )

    # Split the data into training and test sets. (0.75, 0.25) split.
    train, test = train_test_split(data)

    # The predicted column is "quality" which is a scalar from [3, 9]
    train_x = train.drop(["quality"], axis=1)
    test_x = test.drop(["quality"], axis=1)
    train_y = train[["quality"]]
    test_y = test[["quality"]]

    
    alpha = float(sys.argv[1]) if len(sys.argv) > 1 else 0.5
    #alpha = 0.5
    l1_ratio = float(sys.argv[2]) if len(sys.argv) > 2 else 0.5
    #l1_ratio = 0.5

    with mlflow.start_run() as run:
        print("MLflow run experiment_id: {0}".format(run.info.experiment_id))
        print("MLflow run artifact_uri: {0}".format(run.info.artifact_uri))

        lr = ElasticNet(alpha=alpha, l1_ratio=l1_ratio, random_state=42)
        lr.fit(train_x, train_y)

        predicted_qualities = lr.predict(test_x)

        (rmse, mae, r2) = eval_metrics(test_y, predicted_qualities)

        print("Elasticnet model (alpha=%f, l1_ratio=%f):" % (alpha, l1_ratio))
        print("  RMSE: %s" % rmse)
        print("  MAE: %s" % mae)
        print("  R2: %s" % r2)

        mlflow.log_param("alpha", alpha)
        mlflow.log_param("l1_ratio", l1_ratio)
        mlflow.log_metric("rmse", rmse)
        mlflow.log_metric("r2", r2)
        mlflow.log_metric("mae", mae)
        
        # Infer model signature to log it
        signature = mlflow.models.signature.infer_signature(train_x, lr.predict(train_x))

        tracking_url_type_store = urlparse(mlflow.get_tracking_uri()).scheme

        # Model registry does not work with file store
        if tracking_url_type_store != "file":

            # Register the model
            # There are other ways to use the Model Registry, which depends on the use case,
            # please refer to the doc for more information:
            # https://mlflow.org/docs/latest/model-registry.html#api-workflow
            mlflow.sklearn.log_model(lr, "wines-model", registered_model_name="ElasticnetWineModel", signature=signature)
        else:
            mlflow.sklearn.log_model(lr, "model", signature=signature)

Overwriting IUM_08/examples/sklearn_elasticnet_wine/train.py


In [81]:
! ls -l /tmp/mlruns
### Wtyrenujmy model z domyślnymi wartościami parametrów
! cd ./IUM_08/examples/; python sklearn_elasticnet_wine/train.py

total 4
drwxrwxr-x 3 tomek tomek 4096 maj 19 21:31 1
INFO: 's123456' does not exist. Creating a new experiment
MLflow run experiment_id: 2
MLflow run artifact_uri: /tmp/mlruns/2/c15feb5df335490ba990ddd4dd977c1b/artifacts
Elasticnet model (alpha=0.500000, l1_ratio=0.500000):
  RMSE: 0.7931640229276851
  MAE: 0.6271946374319586
  R2: 0.10862644997792614
Registered model 'ElasticnetWineModel' already exists. Creating a new version of this model...
2021/05/19 22:34:48 INFO mlflow.tracking._model_registry.client: Waiting up to 300 seconds for model version to finish creation.                     Model name: ElasticnetWineModel, version 2
Created version '2' of model 'ElasticnetWineModel'.


In [4]:
### I jeszcze raz, tym razem ze zmienionymi wartościami parametrów
! cd ./IUM_08/examples/; for l in {1..9}; do for a in {1..9}; do python sklearn_elasticnet_wine/train.py 0.$a 0.$l; done; done

Elasticnet model (alpha=0.100000, l1_ratio=0.100000):
  RMSE: 0.7128829045893679
  MAE: 0.5462202174984664
  R2: 0.2799376066653344
Elasticnet model (alpha=0.200000, l1_ratio=0.100000):
  RMSE: 0.7268133518615142
  MAE: 0.5586842416161892
  R2: 0.251521166881557
Elasticnet model (alpha=0.300000, l1_ratio=0.100000):
  RMSE: 0.7347397539240514
  MAE: 0.5657315547549873
  R2: 0.23510678899596094
Elasticnet model (alpha=0.400000, l1_ratio=0.100000):
  RMSE: 0.7410782793160982
  MAE: 0.5712718681984227
  R2: 0.22185255063708875
Elasticnet model (alpha=0.500000, l1_ratio=0.100000):
  RMSE: 0.7460550348172179
  MAE: 0.576381895873763
  R2: 0.21136606570632266
Elasticnet model (alpha=0.600000, l1_ratio=0.100000):
  RMSE: 0.7510866447955419
  MAE: 0.5815681289333974
  R2: 0.20069264568704714
Elasticnet model (alpha=0.700000, l1_ratio=0.100000):
  RMSE: 0.7560654760040749
  MAE: 0.5868129921328281
  R2: 0.19006056603695476
Elasticnet model (alpha=0.800000, l1_ratio=0.100000):
  RMSE: 0.760926370

Elasticnet model (alpha=0.900000, l1_ratio=0.700000):
  RMSE: 0.8331069437643933
  MAE: 0.6697424890266508
  R2: 0.016588601539516357
Elasticnet model (alpha=0.100000, l1_ratio=0.800000):
  RMSE: 0.7339712501091269
  MAE: 0.5654097809725043
  R2: 0.23670603806205326
Elasticnet model (alpha=0.200000, l1_ratio=0.800000):
  RMSE: 0.7552646505492441
  MAE: 0.5873472009739388
  R2: 0.19177543499093674
Elasticnet model (alpha=0.300000, l1_ratio=0.800000):
  RMSE: 0.7836957692333741
  MAE: 0.6176788505535867
  R2: 0.12978065429593022
Elasticnet model (alpha=0.400000, l1_ratio=0.800000):
  RMSE: 0.8160164529135189
  MAE: 0.650349905850893
  R2: 0.05652247327326554
Elasticnet model (alpha=0.500000, l1_ratio=0.800000):
  RMSE: 0.8320145539945119
  MAE: 0.6657081587004348
  R2: 0.019165855890777572
Elasticnet model (alpha=0.600000, l1_ratio=0.800000):
  RMSE: 0.8326325509502465
  MAE: 0.6676500690618903
  R2: 0.01770824285088779
Elasticnet model (alpha=0.700000, l1_ratio=0.800000):
  RMSE: 0.8331

In [32]:
### Informacje o przebieagach eksperymentu zostały zapisane w katalogu mlruns
! ls -l IUM_08/examples/mlruns/0 | head

total 16
drwxrwxr-x 6 tomek tomek 4096 maj 17 08:43 375cde31bdd44a45a91fd7cee92ebcda
drwxrwxr-x 6 tomek tomek 4096 maj 17 10:38 b395b55b47fc43de876b67f5a4a5dae9
drwxrwxr-x 6 tomek tomek 4096 maj 17 09:15 b3ead42eca964113b29e7e5f8bcb7bb7
-rw-rw-r-- 1 tomek tomek  151 maj 17 08:43 meta.yaml


In [33]:
! ls -l IUM_08/examples/mlruns/0/375cde31bdd44a45a91fd7cee92ebcda

total 20
drwxrwxr-x 3 tomek tomek 4096 maj 17 08:43 artifacts
-rw-rw-r-- 1 tomek tomek  423 maj 17 08:43 meta.yaml
drwxrwxr-x 2 tomek tomek 4096 maj 17 08:43 metrics
drwxrwxr-x 2 tomek tomek 4096 maj 17 08:43 params
drwxrwxr-x 2 tomek tomek 4096 maj 17 08:43 tags


In [6]:
### Możemy je obejrzeć w przeglądarce uruchamiając interfejs webowy:
### (powinniśmy to wywołać w normalnej konsoli, w jupyter będziemy mieli zablokowany kernel)
! cd IUM_08/examples/; mlflow ui

[2021-05-16 17:58:43 +0200] [118029] [INFO] Starting gunicorn 20.1.0
[2021-05-16 17:58:43 +0200] [118029] [ERROR] Connection in use: ('127.0.0.1', 5000)
[2021-05-16 17:58:43 +0200] [118029] [ERROR] Retrying in 1 second.
[2021-05-16 17:58:44 +0200] [118029] [ERROR] Connection in use: ('127.0.0.1', 5000)
[2021-05-16 17:58:44 +0200] [118029] [ERROR] Retrying in 1 second.
[2021-05-16 17:58:45 +0200] [118029] [ERROR] Connection in use: ('127.0.0.1', 5000)
[2021-05-16 17:58:45 +0200] [118029] [ERROR] Retrying in 1 second.
[2021-05-16 17:58:46 +0200] [118029] [ERROR] Connection in use: ('127.0.0.1', 5000)
[2021-05-16 17:58:46 +0200] [118029] [ERROR] Retrying in 1 second.
[2021-05-16 17:58:47 +0200] [118029] [ERROR] Connection in use: ('127.0.0.1', 5000)
[2021-05-16 17:58:47 +0200] [118029] [ERROR] Retrying in 1 second.
[2021-05-16 17:58:48 +0200] [118029] [ERROR] Can't connect to ('127.0.0.1', 5000)
Running the mlflow server failed. Please see the logs above for details.


Instancja na naszym serwerze: http://tzietkiewicz.vm.wmi.amu.edu.pl:5000/#/

### Wygląd interfejsu webowego
<img width="75%" src="IUM_08/mlflowui.png"/>

### Porównywanie wyników
<img width="75%" src="IUM_08/compare-metrics.png"/>

## Logowanie
 - logowania metryk i parametrów można dokonać m.in. poprzez wywołania Python-owego API: `mlflow.log_param()` i `mlflow.log_metric()`. Więcej dostępnych funkcji: [link](https://mlflow.org/docs/latest/tracking.html#logging-functions)
 - wywołania te muszą nastąpić po wykonaniu [`mlflow.start_run()`](https://mlflow.org/docs/latest/python_api/mlflow.html#mlflow.start_run), najlepiej wewnątrz bloku:
```python
   with mlflow.start_run():
        
        #[...]

        mlflow.log_param("alpha", alpha)
        mlflow.log_param("l1_ratio", l1_ratio)
```
 - jest też możliwość automatycznego logwania dla wybranych bibliotek: https://mlflow.org/docs/latest/tracking.html#automatic-logging

# MLflow Projects
 - MLflow projects to zestaw konwencji i kilku narzędzi
 - ułatwiają one uruchamianie eskperymentów

### Konfiguracja projektu
 - W pliku `MLproject` zapisuje się konfigurację projektu ([specyfikacja](https://mlflow.org/docs/latest/projects.html))
 - Zawiera ona:
    - odnośnik do środowiska, w którym ma być wywołany eksperyment [szczegóły](https://mlflow.org/docs/latest/projects.html#specifying-an-environment):
      - nazwa obrazu Docker
      - albo ścieżka do pliku conda.yaml definiującego środowisko wykonania Conda
    - parametry, z którymi można wywołać eksperyment
    - polecenia służące do wywołania eksperymentu

In [9]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/MLproject
name: tutorial

conda_env: conda.yaml #ścieżka do pliku conda.yaml z definicją środowiska
    
#docker_env:
#  image: mlflow-docker-example-environment

entry_points:
  main:
    parameters:
      alpha: {type: float, default: 0.5}
      l1_ratio: {type: float, default: 0.1}
    command: "python train.py {alpha} {l1_ratio}"
  test:
    parameters:
      alpha: {type: cutoff, default: 0}
    command: "python test.py {cutoff}"

Overwriting IUM_08/examples/sklearn_elasticnet_wine/MLproject


### Środowisko Conda
 </br><img style="height: 50px;" src="img/environments/conda.png"/>
 - https://docs.conda.io
 - Składnia plików conda.yaml definiujących środowisko: https://docs.conda.io/projects/conda/en/4.6.1/user-guide/tasks/manage-environments.html#create-env-file-manually
 - Składnia YAML: [przystępnie](https://learnxinyminutes.com/docs/yaml/), [oficjalnie](https://yaml.org/spec/1.2/spec.html)

In [10]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/conda.yaml
name: tutorial
channels:
  - defaults
dependencies:
  - python=3.6 #Te zależności będą zainstalowane za pomocą conda isntall
  - pip
  - pip: #Te ząś za pomocą pip install
    - scikit-learn==0.23.2
    - mlflow>=1.0

Overwriting IUM_08/examples/sklearn_elasticnet_wine/conda.yaml


### Środowisko docker
- zamiast środowiska Conda możemy również podać nazwę obrazu docker, w którym ma być wywołany eksperyment.
- obraz będzie szukany lokalnie a następnie na DockerHub, lub w innym repozytorium dockera
- składnia specyfikacji ścieżki jest taka sama jak w przypadki poleceń dockera, np. docker pull [link](https://docs.docker.com/engine/reference/commandline/pull/#pull-from-a-different-registry)
- Można również podać katalogi do podmontowania wewnątrz kontenera oraz wartości zmiennych środowiskowych do ustawienia w  kontenerze:
```yaml
docker_env:
   image: mlflow-docker-example-environment
   volumes: ["/local/path:/container/mount/path"]
   environment: [["NEW_ENV_VAR", "new_var_value"], "VAR_TO_COPY_FROM_HOST_ENVIRONMENT"]
```

### Parametry
 - Specyfikacja parametrów w pliku MLproject pozwala na ich walidację i używanie wartości domyślnych
 - Dostępne typy:
   - String
   - Float - dowolna liczba (MLflow waliduje, czy podana wartość jest liczbą)
   - Path - pozwala podawać ścieżki względne (przekształca je na bezwzlędne) do plików lokalnych albo do plików zdalnych (np. do s3://) - zostaną wtedy ściągnięte lokalnie
   - URI - podobnie jak path, ale do rozproszonych systemów plików

- [Składnia](https://mlflow.org/docs/latest/projects.html#specifying-parameters)
  
```yml:
  parameter_name: {type: data_type, default: value}  # Short syntax

  parameter_name:     # Long syntax
     type: data_type
     default: value
```

### Uruchamianie projektu
 - Projekt możemy uruchomić przy pomocy polecenia `mlflow run` ([dokumentacja](https://mlflow.org/docs/latest/cli.html#mlflow-run))
 - Spowoduje to przygotowanie środowiska i uruchomienie eksperymentu wewnątrz środowiska
 - domyślnie zostanie uruchomione polecenie zdefiniowane w "entry point" `main`. Żeby uruchomić inny "entry point", możemy użyć parametru `-e`, np:
 ```bash
 mlflow run sklearn_elasticnet_wine -e test
 ```
 - Parametry do naszego polecenia możemy przekazywać przy pomocy flagi `-P`

In [11]:
!cd IUM_08/examples/; mlflow run sklearn_elasticnet_wine -P alpha=0.42

2021/05/16 17:59:10 INFO mlflow.projects.utils: === Created directory /tmp/tmprq4mdosv for downloading remote URIs passed to arguments of type 'path' ===
2021/05/16 17:59:10 INFO mlflow.projects.backend.local: === Running command 'source /home/tomek/miniconda3/bin/../etc/profile.d/conda.sh && conda activate mlflow-5987e03d4dbaa5faa1a697bb113be9b9bdc39b29 1>&2 && python train.py 0.42 0.1' in run with ID '1860d321ea1545ff8866e4ba199d1712' === 
Elasticnet model (alpha=0.420000, l1_ratio=0.100000):
  RMSE: 0.7420620899060748
  MAE: 0.5722846717246247
  R2: 0.21978513651550236
2021/05/16 17:59:19 INFO mlflow.projects: === Run (ID '1860d321ea1545ff8866e4ba199d1712') succeeded ===


# Zadania [10p pkt]
1. Dodaj do swojego projektu logowanie parametrów i metryk za pomocą MLflow (polecenia `mlflow.log_param` i `mlflow.log_metric`
2. Dodaj plik MLProject definiujący polecenia do trenowania i testowania, ich parametry wywołania oraz środowisko (użyj zdefiniowanego wcześniej obrazu Docker)

## MLflow Models

MLflow Models to konwencja zapisu modeli, która ułatwia potem ich załadowanie i użycie

Rodzaje modeli ("flavors") wspierane przez MLflow:

 - Python Function (python_function)
 - PyTorch (pytorch)
 - TensorFlow (tensorflow)
 - Keras (keras)
 - Scikit-learn (sklearn)
 - Spacy(spaCy)
 - ONNX (onnx)
 - R Function (crate)
 - H2O (h2o)
 - MLeap (mleap)
 - Spark MLlib (spark)
 - MXNet Gluon (gluon)
 - XGBoost (xgboost)
 - LightGBM (lightgbm)
 - CatBoost (catboost)
 - Fastai(fastai)
 - Statsmodels (statsmodels)

### Zapisywanie modelu
Model ML można zapisać w MLflow przy pomocy jednej z dwóch funkcji z pakietu odpowiadającego używanej przez nas bibliotece:
 - `save_model()` - zapisuje model na dysku
 - `log_model()` - zapisuje model razem z innymi informacjami (metrykami, parametrami). W zależności od ustawień ["tracking_uri"](https://mlflow.org/docs/latest/python_api/mlflow.html#mlflow.set_tracking_uri) może być to lokalny folder w `mlruns/ ` lub ścieżka na zdalnym serwerze MLflow

```Python
        mlflow.sklearn.save_model(lr, "my_model")
```

```Python
        mlflow.keras.save_model(lr, "my_model")
```

Wywołanie tej funkcji spowoduje stworzenie katalogu "my_model" zawierającego:
 - plik *MLmodel* zawierający informacje o sposobach, w jaki model można załadować ("flavors") oraz ścieżki do plików związanych z modelem, takich jak:
     - *conda.yaml* - opis środowiska potrzebnego do załadowania modelu
     - *model.pkl* - plik z zserializowanym modelem

Tylko plik *MLmodel* jest specjalnym plikiem MLflow - reszta zależy od konkrentego "flavour"


In [16]:
ls IUM_08/examples/my_model

conda.yaml  MLmodel  model.pkl


In [39]:
! ls -l IUM_08/examples/mlruns/0/b395b55b47fc43de876b67f5a4a5dae9/artifacts/model

total 12
-rw-rw-r-- 1 tomek tomek 153 maj 17 10:38 conda.yaml
-rw-rw-r-- 1 tomek tomek 958 maj 17 10:38 MLmodel
-rw-rw-r-- 1 tomek tomek 641 maj 17 10:38 model.pkl


In [ ]:
# %load IUM_08/examples/mlruns/0/b395b55b47fc43de876b67f5a4a5dae9/artifacts/model/MLmodel
artifact_path: model
flavors:
  python_function:
    env: conda.yaml
    loader_module: mlflow.sklearn
    model_path: model.pkl
    python_version: 3.9.1
  sklearn:
    pickled_model: model.pkl
    serialization_format: cloudpickle
    sklearn_version: 0.24.2
run_id: b395b55b47fc43de876b67f5a4a5dae9
signature:
  inputs: '[{"name": "fixed acidity", "type": "double"}, {"name": "volatile acidity",
    "type": "double"}, {"name": "citric acid", "type": "double"}, {"name": "residual
    sugar", "type": "double"}, {"name": "chlorides", "type": "double"}, {"name": "free
    sulfur dioxide", "type": "double"}, {"name": "total sulfur dioxide", "type": "double"},
    {"name": "density", "type": "double"}, {"name": "pH", "type": "double"}, {"name":
    "sulphates", "type": "double"}, {"name": "alcohol", "type": "double"}]'
  outputs: '[{"type": "tensor", "tensor-spec": {"dtype": "float64", "shape": [-1]}}]'
utc_time_created: '2021-05-17 08:38:41.749670'


In [ ]:
# %load IUM_08/examples/my_model/conda.yaml
channels:
- defaults
- conda-forge
dependencies:
- python=3.9.1
- pip
- pip:
  - mlflow
  - scikit-learn==0.24.2
  - cloudpickle==1.6.0
name: mlflow-env

### Dodatkowe pola w MLmodel


- *utc_time_created* - timestamp z czasem stworzenia modelu
- *run_id*  - ID uruchomienia ("run"), które stworzyło ten model, jeśli model był zapisany za pomocą MLflow Tracking.
- *signature*  - opisa danych wejściowych i wyjściowych w formacie JSON
- *input_example* przykładowe wejście przyjmowane przez model. Można je podać poprzez parametr `input_example` funkcji [log_model](https://mlflow.org/docs/latest/python_api/mlflow.sklearn.html#mlflow.sklearn.log_model)



In [50]:
import mlflow
import pandas as pd
model = mlflow.sklearn.load_model("IUM_08/examples/mlruns/0/b395b55b47fc43de876b67f5a4a5dae9/artifacts/model")
csv_url = "http://archive.ics.uci.edu/ml/machine-learning-databases/wine-quality/winequality-red.csv"
data = pd.read_csv(csv_url, sep=";")
model.predict(data.drop(["quality"], axis=1).head())

array([5.57688397, 5.50664777, 5.52550482, 5.50431125, 5.57688397])

### Serwowanie modeli

In [7]:
!cd IUM_08/examples/; mlflow models --help

Usage: mlflow models [OPTIONS] COMMAND [ARGS]...

  Deploy MLflow models locally.

  To deploy a model associated with a run on a tracking server, set the
  MLFLOW_TRACKING_URI environment variable to the URL of the desired server.

Options:
  --help  Show this message and exit.

Commands:
  build-docker  **EXPERIMENTAL**: Builds a Docker image whose default...
  predict       Generate predictions in json format using a saved MLflow...
  prepare-env   **EXPERIMENTAL**: Performs any preparation necessary to...
  serve         Serve a model saved with MLflow by launching a webserver on...


In [8]:
!cd IUM_08/examples/; mlflow models serve --help

Usage: mlflow models serve [OPTIONS]

  Serve a model saved with MLflow by launching a webserver on the specified
  host and port. The command supports models with the ``python_function`` or
  ``crate`` (R Function) flavor. For information about the input data
  formats accepted by the webserver, see the following documentation:
  https://www.mlflow.org/docs/latest/models.html#built-in-deployment-tools.

  You can make requests to ``POST /invocations`` in pandas split- or record-
  oriented formats.

  Example:

  .. code-block:: bash

      $ mlflow models serve -m runs:/my-run-id/model-path &

      $ curl http://127.0.0.1:5000/invocations -H 'Content-Type:
      application/json' -d '{         "columns": ["a", "b", "c"],
      "data": [[1, 2, 3], [4, 5, 6]]     }'

Options:
  -m, --model-uri URI  URI to the model. A local path, a 'runs:/' URI, or a
                       remote storage URI (e.g., an 's3://' URI). For more
                       information about supported remote URI

In [54]:
import pandas as pd
csv_url = "http://archive.ics.uci.edu/ml/machine-learning-databases/wine-quality/winequality-red.csv"
data = pd.read_csv(csv_url, sep=";").drop(["quality"], axis=1).head(1).to_json(orient='split')
print(data)

{"columns":["fixed acidity","volatile acidity","citric acid","residual sugar","chlorides","free sulfur dioxide","total sulfur dioxide","density","pH","sulphates","alcohol"],"index":[0],"data":[[7.4,0.7,0.0,1.9,0.076,11.0,34.0,0.9978,3.51,0.56,9.4]]}


In [57]:
!curl http://127.0.0.1:5003/invocations -H 'Content-Type: application/json' -d '{\
        "columns":[\
            "fixed acidity","volatile acidity","citric acid","residual sugar","chlorides","free sulfur dioxide","total sulfur dioxide","density","pH","sulphates","alcohol"],\
            "index":[0],\
            "data":[[7.4,0.7,0.0,1.9,0.076,11.0,34.0,0.9978,3.51,0.56,9.4]]}'

[5.576883967129615]

```
$ cd IUM_08/examples/
$ mlflow models serve -m my_model
2021/05/17 08:52:07 INFO mlflow.models.cli: Selected backend for flavor 'python_function'
2021/05/17 08:52:07 INFO mlflow.pyfunc.backend: === Running command 'source /home/tomek/miniconda3/bin/../etc/profile.d/conda.sh && conda activate mlflow-503f0c7520a32f054a9d168bd099584a9439de9d 1>&2 && gunicorn --timeout=60 -b 127.0.0.1:5003 -w 1 ${GUNICORN_CMD_ARGS} -- mlflow.pyfunc.scoring_server.wsgi:app'
[2021-05-17 08:52:07 +0200] [291217] [INFO] Starting gunicorn 20.1.0
[2021-05-17 08:52:07 +0200] [291217] [INFO] Listening at: http://127.0.0.1:5003 (291217)
[2021-05-17 08:52:07 +0200] [291217] [INFO] Using worker: sync
[2021-05-17 08:52:07 +0200] [291221] [INFO] Booting worker with pid: 291221
```

## MLflow Registry
 - umożliwia [zapisywanie](https://mlflow.org/docs/latest/model-registry.html#adding-an-mlflow-model-to-the-model-registry) i [ładowanie](https://mlflow.org/docs/latest/model-registry.html#fetching-an-mlflow-model-from-the-model-registry) modeli z centralnego rejestru
 - Modele można też serwować bezpośrednio z rejestru:

```bash
#!/usr/bin/env sh

# Set environment variable for the tracking URL where the Model Registry resides
export MLFLOW_TRACKING_URI=http://localhost:5000

# Serve the production model from the model registry
mlflow models serve -m "models:/sk-learn-random-forest-reg-model/Production"
```

- Żeby było to możliwe, musimy mieć uruchomiony [serwer MLflow](https://mlflow.org/docs/latest/tracking.html#tracking-server)
- Umożliwia zarządzanie wersjami modeli i oznaczanie ich różnymi fazami, np. "Staging", "Production"

## Zadania
1. [2 pkt] Dodaj do joba treningowego wywołania MLflow, tak, żeby przy każdym uruchomieniu stworzyć i zarchiwizować katalog z modelem. Plik MLmodel powinien zawierać pola:
 - signature
 - input_example

   Folder powinien również zawierać definicję środowiska - conda lub docker, umożliwiającego uruchomienie projektu.

2. [6 pkt] Wybierz jedną osobę z grupy. Załóżmy, że Twoje ID to s123456 a jej s654321. Stwórz na Jenkinsie projekt `s123456-predict-s654321`, w którym:
 - pobierzesz artefakt z zapisanym modelem z joba osoby s654321
 - dokonasz na nim predykcji danych wejściowych podanych w formacie json jako parametr zadania Jenkinsowego. Domyślną wartością tego parametru niech będą przykładowe dane wejściowe z `input_example`
 
3. [1 pkt] Zarejestruj swój model w MLflow registry

4. [6 pkt] Stwórz na Jenkinsie projekt `s123456-predict-s654321-from-registry`, który zrealizuje to samo zadanie co `s123456-predict-s654321`, ale tym razem pobierze model z rejestru MLflow zamiast z artefaktów Jenkinsa

Dane do konfiguracji MLflow registry

- Podgląd w przeglądarce: http://tzietkiewicz.vm.wmi.amu.edu.pl/#/
   - user: `student`
   - hasło: IUM@2021

- Tracking URI:
   - Python: `mlflow.set_tracking_uri("http://172.17.0.1:5000")`
   - CLI: `export MLFLOW_TRACKING_URI=http://172.17.0.1:5000`
   
- Żeby klient MLflow działający w kontenerze docker mógł zapisywać i pdczytywać artefakty, muszą Państwo podmonotwać katalog `/tmp/mlruns` i `/mlruns` (ten drugi po to, żeby po restarcie serwera katalog nie został wyczyszczony)
- Proszę ustawić nazwę eksperymentu na numer indeksu, dzięki temu każdy z Państwa będzie widział swoje eksperymenty oddzielnie:
`mlflow.set_experiment("s123456")`